In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px
import seaborn as sns

Primero leemos tanto los datos 'crudos' como los procesados, ya que los primeros se ecuentran en formato "wide", y puede ser util para detectar tendencias a lo largo del tiempo:

In [2]:
processed_path = '../data/processed/processed_data_energy.csv'
raw_path = '../data/raw/Dataset_GCRNO.csv'

df = pd.read_csv(processed_path)
raw_df = pd.read_csv(raw_path)

Antes de comenzar, convertimos nuestra columna `FECHA`, del dataframe `raw_df` a una de tipo datetime, para facilitar el análisis temporal de los datos

In [3]:
# Diccionario para meses
dict_mes = {'ene':'01',
            'feb':'02',
            'mar':'03',
            'abr':'04',
            'may':'05',
            'jun':'06',
            'jul':'07',
            'ago':'08',
            'sep':'09',
            'oct':'10',
            'nov':'11',
            'dic':'12'
        }

raw_df['FECHA'] = raw_df['FECHA'].replace(dict_mes, regex=True)
raw_df['FECHA'] = pd.to_datetime(raw_df['FECHA'], format='%d-%m-%y')

In [4]:
raw_df.head()

FECHA  DEM_GCRNO_H0  DEM_GCRNO_H1  DEM_GCRNO_H2  DEM_GCRNO_H3  \
0 2007-01-01          1394          1297          1255          1222   
1 2007-01-02          1261          1177          1128          1098   
2 2007-01-03          1451          1376          1308          1277   
3 2007-01-04          1479          1390          1325          1284   
4 2007-01-05          1497          1394          1323          1271   

   DEM_GCRNO_H4  DEM_GCRNO_H5  DEM_GCRNO_H6  DEM_GCRNO_H7  DEM_GCRNO_H8  ...  \
0          1168          1128          1100          1083          1076  ...   
1          1078          1071          1079          1097          1151  ...   
2          1258          1246          1258          1286          1351  ...   
3          1268          1260          1261          1285          1343  ...   
4          1242          1236          1245          1292          1344  ...   

   LUNES_FESTIVO  MARTES_POSTFESTIVO  SEMANA_SANTA  1_MAYO  10_MAYO  16_SEP  \
0              0                   0             0       0        0       0   
1              0                   0             0       0        0       0   
2              0                   0             0       0        0       0   
3              0                   0             0       0        0       0   
4              0                   0             0       0        0       0   

   2_NOV.  PRE-NAVIDAD_Y_NEW_YEAR  NAVIDAD_Y_NEW_YEAR  POST-NAVIDAD_Y_NEW_YEAR  
0       0                       0                   1                        0  
1       0                       0                   0                        1  
2       0                       0                   0                        0  
3       0                       0                   0                        0  
4       0                       0                   0                        0  

[5 rows x 49 columns]

## Evolución de la demanda de energia promedio a lo largo del tiempo

En nuestro dataset (raw), contamos con datos sobre la demanda de energia diaria durante cada hora a lo largo de los años. A partir de estos datos, podemos obtener un valor de demanda "promedio" a lo largo del dia. 

Después, podemos tratar de visualizar la evolución de este valor a lo largo del tiempo, para tratar de identificar tendencias que pudieran ocasionar problemas a futuro a nuestro modelo.

In [5]:
column_list = []

# Generamos una lista de las columnas con la demanda por hora
for column in raw_df.columns:
    if 'DEM_GCRNO' in column:
        column_list.append(column)

print(column_list)

['DEM_GCRNO_H0', 'DEM_GCRNO_H1', 'DEM_GCRNO_H2', 'DEM_GCRNO_H3', 'DEM_GCRNO_H4', 'DEM_GCRNO_H5', 'DEM_GCRNO_H6', 'DEM_GCRNO_H7', 'DEM_GCRNO_H8', 'DEM_GCRNO_H9', 'DEM_GCRNO_H10', 'DEM_GCRNO_H11', 'DEM_GCRNO_H12', 'DEM_GCRNO_H13', 'DEM_GCRNO_H14', 'DEM_GCRNO_H15', 'DEM_GCRNO_H16', 'DEM_GCRNO_H17', 'DEM_GCRNO_H18', 'DEM_GCRNO_H19', 'DEM_GCRNO_H20', 'DEM_GCRNO_H21', 'DEM_GCRNO_H22', 'DEM_GCRNO_H23']


In [6]:
# Utilizando la lista generada, obtenemos el promedio de cada fila, y lo agregamos a una nueva columna
raw_df['DEM_PROM_GCRNO'] = raw_df[column_list].mean(axis=1)

In [7]:
raw_df.head()

FECHA  DEM_GCRNO_H0  DEM_GCRNO_H1  DEM_GCRNO_H2  DEM_GCRNO_H3  \
0 2007-01-01          1394          1297          1255          1222   
1 2007-01-02          1261          1177          1128          1098   
2 2007-01-03          1451          1376          1308          1277   
3 2007-01-04          1479          1390          1325          1284   
4 2007-01-05          1497          1394          1323          1271   

   DEM_GCRNO_H4  DEM_GCRNO_H5  DEM_GCRNO_H6  DEM_GCRNO_H7  DEM_GCRNO_H8  ...  \
0          1168          1128          1100          1083          1076  ...   
1          1078          1071          1079          1097          1151  ...   
2          1258          1246          1258          1286          1351  ...   
3          1268          1260          1261          1285          1343  ...   
4          1242          1236          1245          1292          1344  ...   

   MARTES_POSTFESTIVO  SEMANA_SANTA  1_MAYO  10_MAYO  16_SEP  2_NOV.  \
0                   0             0       0        0       0       0   
1                   0             0       0        0       0       0   
2                   0             0       0        0       0       0   
3                   0             0       0        0       0       0   
4                   0             0       0        0       0       0   

   PRE-NAVIDAD_Y_NEW_YEAR  NAVIDAD_Y_NEW_YEAR  POST-NAVIDAD_Y_NEW_YEAR  \
0                       0                   1                        0   
1                       0                   0                        1   
2                       0                   0                        0   
3                       0                   0                        0   
4                       0                   0                        0   

   DEM_PROM_GCRNO  
0     1165.250000  
1     1335.416667  
2     1452.125000  
3     1457.750000  
4     1458.208333  

[5 rows x 50 columns]

Con esta nueva columna, podemos tratar de visualizar la evolución de la demanda promedio diaria a lo largo del tiempo:

In [10]:
# Creando un gráfico de líneas para ver el comportamiento por día
fig = px.line(raw_df, x='FECHA', y='DEM_PROM_GCRNO',
              labels={
                  'DEM_PROM_GCRNO': 'Demanda promedio diaria, MW',
                  'FECHA': 'Fecha'
              },
              title='Demanda Promedio Diaria de energia, Región Noroeste')

fig.show()

En la gráfica anterior, podemos apreciar que:
- Generalmente es durante los meses de verano que se observa una mayor demanda diaria promedio de energía.
- Podemos apreciar una tendencia estacional a lo largo de los años, ya que observamos que el patrón mencionado en el punto anterior se repite a lo largo del tiempo.
- Sin embargo, parece haber una tendenia a la alta, incluso tomando en cuenta la estacionalidad de la demanda. Esto es algo que verificaremos más adelante.

## Visualizando la evolución de las temperaturas máximas de la región noroeste

Utilizando una metodología similar a la del punto anterior, podemos analizar/visualizar el comportamiento de las temperaturas máximas de la región.

In [13]:
column_list_tmax = []

# Generamos una lista de las columnas con la temperatura maxima
for column in raw_df.columns:
    if 'TMAX' in column:
        column_list_tmax.append(column)

print(column_list_tmax)

['TMAX-CAB', 'TMAX-HMO', 'TMAX-OBR', 'TMAX-LMO', 'TMAX-CUL']


In [15]:
tmax_df = raw_df[['FECHA'] + column_list_tmax]
tmax_df.head()

FECHA  TMAX-CAB  TMAX-HMO  TMAX-OBR  TMAX-LMO  TMAX-CUL
0 2007-01-01      21.0      22.0      25.0      30.0      29.0
1 2007-01-02      21.0      22.0      22.0      22.0      27.0
2 2007-01-03      22.0      22.0      23.0      25.0      27.0
3 2007-01-04      22.0      24.0      26.0      26.0      28.0
4 2007-01-05      24.0      21.0      25.0      28.0      29.0

In [22]:
tmax_df_melt = tmax_df.melt(id_vars='FECHA', value_name='value')
tmax_df_melt['ciudad'] = tmax_df_melt['variable'].str.split('-').str[1]
tmax_df_melt.drop(columns=['variable'], inplace=True)
tmax_df_melt.head()

FECHA  value ciudad
0 2007-01-01   21.0    CAB
1 2007-01-02   21.0    CAB
2 2007-01-03   22.0    CAB
3 2007-01-04   22.0    CAB
4 2007-01-05   24.0    CAB

Con esto, podemos visualizar la evolución de las temperaturas máximas en la región a través del tiempo:

In [23]:
# Creando un gráfico de líneas para ver el comportamiento por día
fig = px.line(tmax_df_melt, x='FECHA', y='value',color='ciudad',
              labels={
                  'value': 'Temperatura máxima, °C',
                  'FECHA': 'Fecha',
                  'ciudad': 'Ciudad'
              },
              title='Temperatura máxima diaria, Región Noroeste')

fig.show()

En la figura anterior podemos apreciar que:
- Si bien la demanda de energía parece aumentar a lo largo del tiempo, a simple vista no parece haber un aumento notable en las temperaturas máximas registradas a lo largo del tiempo.
- Fuera de unos cuantos outliers, parece haber una estacionalidad constante en los datos de las temperaturas máximas.

Podemos realizar de nuevo el mismo procedimiento, pero ahora para las temperaturas mínimas:

In [14]:
column_list_tmin = []

# Generamos una lista de las columnas con la demanda por hora
for column in raw_df.columns:
    if 'TMIN' in column:
        column_list_tmin.append(column)

print(column_list_tmin)

['TMIN-CAB', 'TMIN-HMO', 'TMIN-OBR', 'TMIN-LMO', 'TMIN-CUL']


In [24]:
tmin_df = raw_df[['FECHA'] + column_list_tmin]
tmin_df.head()

FECHA  TMIN-CAB  TMIN-HMO  TMIN-OBR  TMIN-LMO  TMIN-CUL
0 2007-01-01       2.0       9.0       8.0      10.0       9.0
1 2007-01-02       2.0       7.0       7.0      11.0      14.0
2 2007-01-03       6.0       6.0      10.0      11.0      15.0
3 2007-01-04       5.0      11.0       9.0      11.0      10.0
4 2007-01-05       6.0      10.0       9.0      10.0      10.0

In [25]:
tmin_df_melt = tmin_df.melt(id_vars='FECHA', value_name='value')
tmin_df_melt['ciudad'] = tmin_df_melt['variable'].str.split('-').str[1]
tmin_df_melt.drop(columns=['variable'], inplace=True)
tmin_df_melt.head()

FECHA  value ciudad
0 2007-01-01    2.0    CAB
1 2007-01-02    2.0    CAB
2 2007-01-03    6.0    CAB
3 2007-01-04    5.0    CAB
4 2007-01-05    6.0    CAB

In [26]:
# Creando un gráfico de líneas para ver el comportamiento por día
fig = px.line(tmin_df_melt, x='FECHA', y='value',color='ciudad',
              labels={
                  'value': 'Temperatura mínima, °C',
                  'FECHA': 'Fecha',
                  'ciudad': 'Ciudad'
              },
              title='Temperatura máxima diaria, Región Noroeste')

fig.show()